In [1]:
import os
import torch

try:
  from google.colab import drive
  drive.mount('/content/drive')

  os.chdir('/content/drive/MyDrive/GitHub/kornia')
except Exception:   # Not run on Google Colab
  import getpass
  if getpass.getuser() == 'vscode':       # Running in container
    os.chdir('/workspaces/kornia/')
  else:                                   # Running in virtual environment
    os.chdir(os.path.join(os.path.expanduser('~'), 'Documents/Git/kornia/'))

  print(os.getcwd())
  import sys
  sys.path.insert(0, os.getcwd())

/home/yhollander/Documents/Git/kornia


In [2]:
from kornia.nerf.camera_utils import create_spline_curve, create_spiral_path
from kornia.nerf.colmap_parser import parse_colmap_output, parse_colmap_points_3d
from kornia.nerf.rays import FocalAxisRay, sample_lengths, sample_ray_points

## Load Colmap outputs

### Scene Colmap camera poses

In [10]:
scene_name = 'flower_4'
# scene_name = 'head_sculpture4'
# scene_name = 'lego'

data_dir = 'kornia/nerf/kornia_nerf_data/'

scene_dir = os.path.join(data_dir, scene_name)

cameras_path = os.path.join(scene_dir, 'cameras.txt')
images_path = os.path.join(scene_dir, 'images.txt')

In [11]:
img_names, cameras = parse_colmap_output(cameras_path, images_path, 'cpu', torch.float32, sort_by_image_names=True)
print(img_names)


['image000.png', 'image001.png', 'image002.png', 'image003.png', 'image004.png', 'image005.png', 'image006.png', 'image007.png', 'image008.png', 'image009.png', 'image010.png', 'image011.png', 'image012.png', 'image013.png', 'image014.png', 'image015.png', 'image016.png', 'image017.png', 'image018.png', 'image019.png', 'image020.png', 'image021.png', 'image022.png', 'image023.png', 'image024.png', 'image025.png', 'image026.png', 'image027.png', 'image028.png', 'image029.png', 'image030.png', 'image031.png', 'image032.png', 'image033.png']


In [12]:
cameras_new = create_spline_curve(cameras, 30)

# cameras_new = create_spiral_path(cameras, rad=1., num_views=30, num_circles=2)

In [13]:
# Camera origins
origins = cameras.origins().squeeze(-1)
origins_new = cameras_new.origins().squeeze(-1)

print(cameras.translation_vector.shape)
print(cameras.origins().shape)

torch.Size([34, 3, 1])
torch.Size([34, 3, 1])


### Colmap point 3D cloud

In [14]:
points_3d_path = os.path.join(scene_dir, 'points3D.txt')
points_3d_sparse_cloud = parse_colmap_points_3d(points_3d_path, 'cpu', torch.float32)

print(points_3d_sparse_cloud.shape)

torch.Size([17308, 3])


#### Analyze 3d cloud depths from cameras

In [23]:
from kornia.nerf.rays import analyze_points_3d

min_depth, max_depth = analyze_points_3d(points_3d_sparse_cloud, cameras)
print(min_depth)
print(max_depth)

min_depth_cameras = torch.mean(min_depth).item()
max_depth_cameras = torch.mean(max_depth).item()

print(min_depth_cameras, max_depth_cameras)

tensor([23.5875, 23.5916, 23.9330, 24.1255, 24.1444, 24.6028, 24.4242, 24.3261,
        23.6356, 23.7628, 24.0650, 24.3690, 24.8067, 24.7035, 24.5082, 24.5306,
        24.4695, 24.6810, 25.1130, 25.3281, 25.0996, 24.7831, 25.0106, 25.0929,
        25.2651, 24.9608, 25.4210, 25.1539, 25.6568, 25.8451, 26.0135, 26.3289,
        26.1955, 26.3476])
tensor([114.4846, 114.6773, 114.8753, 114.7723, 114.7291, 114.4951, 113.5926,
        113.1852, 112.4294, 112.9056, 113.6035, 114.4867, 115.3274, 115.5443,
        116.0156, 116.6182, 117.6196, 117.7742, 117.8305, 117.4484, 116.7575,
        116.1347, 115.6637, 114.7719, 114.6282, 114.0339, 114.8547, 115.5798,
        116.3699, 116.9810, 117.5032, 118.2530, 118.9287, 119.7742])
24.82007598876953 115.6661376953125


## Create focal rays for cameras

In [17]:
# Focal axes for cameras
focal_axis_rays = FocalAxisRay(max_depth_cameras, min_depth = min_depth_cameras, corner_rays=True)
focal_axis_rays.calc_ray_params(cameras)

lengths = sample_lengths(focal_axis_rays.origins.shape[0], 2, irregular=False, device='cpu', 
                         dtype=torch.float32)
points_3d_rays = sample_ray_points(
    focal_axis_rays.origins,
    focal_axis_rays.directions,
    lengths,
)

print(points_3d_rays.shape)

torch.Size([500, 2, 3])


In [18]:
# Resampling rays for new cameras
focal_axis_rays.calc_ray_params(cameras_new)

lengths = sample_lengths(focal_axis_rays.origins.shape[0], 2, irregular=False, device='cpu', 
                         dtype=torch.float32)
points_3d_rays_new = sample_ray_points(
    focal_axis_rays.origins,
    focal_axis_rays.directions,
    lengths,
)

## Ploting cameras and rays

In [21]:
from plotly.subplots import make_subplots
import plotly.graph_objects as go

fig = make_subplots(rows=1, cols=2, specs=[[{"type": "scene"}, {"type": "scene"}]])

## Original cameras
fig.add_trace(go.Scatter3d(x=origins[:, 0], y=origins[:, 1], z=origins[:, 2]), row=1, col=1)

# Focal lines
for i in range(points_3d_rays.shape[0]):
    fig.add_trace(go.Scatter3d(x=points_3d_rays[i, 0:2, 0], y=points_3d_rays[i, 0:2, 1], z=points_3d_rays[i, 0:2, 2], mode='lines'))

## New cameras
fig.add_trace(go.Scatter3d(x=origins_new[:, 0], y=origins_new[:, 1], z=origins_new[:, 2]), row=1, col=2)

# Focal lines
for i in range(points_3d_rays_new.shape[0]):
    fig.add_trace(go.Scatter3d(x=points_3d_rays_new[i, 0:2, 0], y=points_3d_rays_new[i, 0:2, 1], z=points_3d_rays_new[i, 0:2, 2], mode='lines'), row=1, col=2)

## Point cloud
fig.add_trace(go.Scatter3d(x=points_3d_sparse_cloud[:, 0, 0], y=points_3d_sparse_cloud[:, 0, 1], z=points_3d_sparse_cloud[:, 0, 2], mode='markers', marker_size=2), row=1, col=1)
fig.add_trace(go.Scatter3d(x=points_3d_sparse_cloud[:, 0, 0], y=points_3d_sparse_cloud[:, 0, 1], z=points_3d_sparse_cloud[:, 0, 2], mode='markers', marker_size=2), row=1, col=2)

fig.show()